# **General cells no matter which model or dataset**

In [ ]:
import tensorflow as tf
from tensorflow.keras.layers import TimeDistributed, LSTM, Dense, Flatten ,Conv3D, MaxPooling3D, Dropout, BatchNormalization
from tensorflow.keras.applications import ResNet50
from tensorflow.keras.models import Sequential
from tensorflow.keras.preprocessing.sequence import pad_sequences
import numpy as np
import cv2
from tensorflow.keras.models import load_model
from sklearn.model_selection import train_test_split


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
def get_frame_count(video_path):
    # Open the video file
    cap = cv2.VideoCapture(video_path)

    # Check if the video opened successfully
    if not cap.isOpened():
        print(f"Error: Cannot open video {video_path}")
        return None

    # Get the total number of frames
    frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))

    # Release the video capture object
    cap.release()

    return frame_count

In [ ]:
class NormalModel:
  def __init__(self, input_size = (40,224,224,3), num_classes=1):

        self.model = Sequential()


  def preprocess_video(self, video_path, num_frames=40):
      """Read the video, sample 50 frames, and resize them to 224x224."""
      cap = cv2.VideoCapture(video_path)
      total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))

      # Calculate frame indices to sample uniformly across the video
      frame_indices = np.linspace(0, total_frames - 1, num=num_frames, dtype=int)
      sampled_frames = []

      for idx in frame_indices:
          cap.set(cv2.CAP_PROP_POS_FRAMES, idx)  # Set the frame position
          ret, frame = cap.read()
          if not ret:
              print(f"Warning: Could not read frame {idx} from {video_path}.")
              # break
              continue

          # Resize the frame to 224x224 (to match ResNet50 input size)
          frame = cv2.resize(frame, (224, 224))
          sampled_frames.append(frame)

      cap.release()

      # If fewer frames were read, pad with zeros
      if len(sampled_frames) < num_frames:
          padding = np.zeros((num_frames - len(sampled_frames), 224, 224, 3))
          sampled_frames = np.concatenate([sampled_frames, padding], axis=0)

      return np.array(sampled_frames)



  def train(self, video_paths, labels, batch_size=30):
      """Train the model in mini-batches to manage memory."""
      for i in range(0, len(video_paths), batch_size):
          batch_videos = video_paths[i:i + batch_size]
          batch_labels = labels[i:i + batch_size]

          # Preprocess each video and collect as a batch
          X_batch = np.array([self.preprocess_video(path) for path in batch_videos])
          y_batch = np.array(batch_labels)

          # Train the model on the current batch and capture the loss and accuracy
          loss, accuracy = self.model.train_on_batch(X_batch, y_batch)

          # Print or log the training progress
          print(f"Batch {i // batch_size + 1}: Loss = {loss:.4f}, Accuracy = {accuracy:.4f}")


  def test(self, video_paths, batch_size=32):
      """Test the model on the given videos in batches."""
      predictions = []

      for i in range(0, len(video_paths), batch_size):
          batch_paths = video_paths[i:i + batch_size]

          X_batch = np.array([self.preprocess_video(path) for path in batch_paths])

          batch_predictions = self.model.predict(X_batch)

          predictions.extend(batch_predictions[:, 0].tolist())

      return predictions


  def load_model(self, filepath):
    """Load the entire model from the specified file path."""
    self.model = load_model(filepath)
    print(f"Model loaded from {filepath}.")

  def save_model(self, filepath):
    """Save the entire model to the specified file path."""
    self.model.save(filepath)
    print(f"Model saved to {filepath}.")


In [ ]:

def calculate_accuracy(predictions, labels, threshold=0.5):
    """
    Calculate the accuracy of predictions given true labels.

    Args:
        predictions (np.array): The predicted probabilities (output from the model).
        labels (np.array): The true labels for the data.
        threshold (float): The threshold to determine class predictions.

    Returns:
        float: The accuracy as a percentage.
    """

    predictions = np.array(predictions)
    labels = np.array(labels)

    predicted_classes = (predictions >= threshold).astype(int)

    accuracy = np.mean(predicted_classes == labels) * 100
    return accuracy

In [ ]:
!unzip /content/drive/MyDrive/Models/new_model.zip -d /content/                  # for single LSTM + CNN model

!mv /content/model.h5 /content/A_model.h5             # rename it, model Nourhan and this model have the same name

Archive:  /content/drive/MyDrive/Models/new_model.zip
 extracting: /content/model.h5       


In [ ]:
!unzip /content/drive/MyDrive/Models/Nourhan_model.zip -d /content/              # for Bi LSTM + CNN model

Archive:  /content/drive/MyDrive/Models/Nourhan_model.zip
 extracting: /content/model.h5       


In [ ]:
!unzip /content/drive/MyDrive/Models/3D_CNN_model.zip -d /content/               # for 3D CNN architecture model

Archive:  /content/drive/MyDrive/Models/3D_CNN_model.zip
 extracting: /content/3D_CNN_model.h5  


In [ ]:
!unzip /content/drive/MyDrive/Models/pre_3D_model.zip -d /content/               # for pretrained 3D model

Archive:  /content/drive/MyDrive/Models/pre_3D_model.zip
 extracting: /content/pre_3D_model.h5  


In [ ]:
!unzip /content/drive/MyDrive/Models/pre_3D_model_v2.zip -d /content/               # for pretrained 3D model

Archive:  /content/drive/MyDrive/Models/pre_3D_model_v2.zip
 extracting: /content/content/pre_3D_model_v2.h5  


# **For Hockey fights Dataset**

In [ ]:
!kaggle datasets download -d yassershrief/hockey-fight-vidoes --unzip -p /content/hockey_fight

import os

base_dir = '/content/hockey_fight'
for root, dirs, files in os.walk(base_dir):
    print(root, ":", len(files), "files")
BASE_DIR = '/content/hockey_fight/data'

Dataset URL: https://www.kaggle.com/datasets/yassershrief/hockey-fight-vidoes
License(s): unknown
 92% 150M/164M [00:01<00:00, 74.1MB/s]
100% 164M/164M [00:01<00:00, 92.9MB/s]
/content/hockey_fight : 0 files
/content/hockey_fight/data : 1000 files


In [ ]:
def prepare_data(base_path):
    categories = {
        "Violence": 0,         # Class 0
        "NonViolence": 1       # Class 1
    }

    file_paths = []
    labels = []

    # Iterate through all video files in the base directory
    for file_name in os.listdir(base_path):

            if file_name.lower().startswith('f'):
                label = categories["Violence"]
            else:
                label = categories["NonViolence"]

            file_paths.append(os.path.join(base_path, file_name))
            labels.append(label)

    # Convert lists to numpy arrays
    file_paths = np.array(file_paths)
    labels = np.array(labels)

    # Shuffle data while keeping labels in sync
    indices = np.arange(len(file_paths))  # Create an array of indices
    np.random.shuffle(indices)             # Shuffle the indices

    # Use the shuffled indices to rearrange file_paths and labels
    shuffled_file_paths = file_paths[indices]
    shuffled_labels = labels[indices]

    return shuffled_file_paths, shuffled_labels


In [ ]:

file_paths_1 , labels_1 = prepare_data(BASE_DIR)

for path in file_paths_1:
  frame_count = get_frame_count(path)
  print(f"Total number of frames: {frame_count}")

# /content/real_life_violence/Real Life Violence Dataset/

Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 42
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
Total number of frames: 41
T

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(file_paths_1 , labels_1 , test_size=0.15 , stratify=labels_1)


# **For Real-life Violence Dataset**

In [ ]:
!kaggle datasets download -d mohamedmustafa/real-life-violence-situations-dataset --unzip -p /content/real_life_violence

import os

base_dir = '/content/real_life_violence'
for root, dirs, files in os.walk(base_dir):
    print(root, ":", len(files), "files")
BASE_DIR = '/content/real_life_violence/Real Life Violence Dataset'

Dataset URL: https://www.kaggle.com/datasets/mohamedmustafa/real-life-violence-situations-dataset
License(s): copyright-authors
100% 3.58G/3.58G [01:24<00:00, 25.4MB/s]
100% 3.58G/3.58G [01:24<00:00, 45.4MB/s]
/content/real_life_violence : 0 files
/content/real_life_violence/real life violence situations : 0 files
/content/real_life_violence/real life violence situations/Real Life Violence Dataset : 0 files
/content/real_life_violence/real life violence situations/Real Life Violence Dataset/Violence : 1000 files
/content/real_life_violence/real life violence situations/Real Life Violence Dataset/NonViolence : 1000 files
/content/real_life_violence/Real Life Violence Dataset : 0 files
/content/real_life_violence/Real Life Violence Dataset/Violence : 1000 files
/content/real_life_violence/Real Life Violence Dataset/NonViolence : 1000 files


In [ ]:
def prepare_data(base_path):
    label_map = {
        "Violence": 0,            # Class 0
        "NonViolence": 1          # Class 1
    }

    file_paths = []
    labels = []

    # Loop through each class folder (Normal, Violence, Weaponized)
    for class_name, label in label_map.items():
        class_path = os.path.join(base_path, class_name)

        # Collect all video file paths in the current class folder
        for file_name in os.listdir(class_path):
            if file_name.endswith(('.mp4', '.avi', '.mov')):  # Adjust for valid video formats
                file_paths.append(os.path.join(class_path, file_name))
                labels.append(label)


    file_paths = np.array(file_paths)

    labels = np.array(labels)

    # Shuffle data while keeping labels in sync
    indices = np.arange(len(file_paths))  # Create an array of indices
    np.random.shuffle(indices)             # Shuffle the indices

    # Use the shuffled indices to rearrange file_paths and labels
    shuffled_file_paths = file_paths[indices]
    shuffled_labels = labels[indices]
    # Convert lists to numpy arrays for easier handling
    return shuffled_file_paths, shuffled_labels

In [ ]:

file_paths_2 , labels_2 = prepare_data(BASE_DIR)

for path in file_paths_2:
  frame_count = get_frame_count(path)
  print(f"Total number of frames: {frame_count}")



Total number of frames: 120
Total number of frames: 113
Total number of frames: 150
Total number of frames: 55
Total number of frames: 145
Total number of frames: 112
Total number of frames: 146
Total number of frames: 129
Total number of frames: 129
Total number of frames: 125
Total number of frames: 125
Total number of frames: 147
Total number of frames: 150
Total number of frames: 153
Total number of frames: 177
Total number of frames: 115
Total number of frames: 95
Total number of frames: 145
Total number of frames: 115
Total number of frames: 55
Total number of frames: 147
Total number of frames: 141
Total number of frames: 123
Total number of frames: 132
Total number of frames: 108
Total number of frames: 143
Total number of frames: 115
Total number of frames: 125
Total number of frames: 115
Total number of frames: 135
Total number of frames: 102
Total number of frames: 153
Total number of frames: 133
Total number of frames: 135
Total number of frames: 55
Total number of frames: 

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(file_paths_2 , labels_2 , test_size=0.20 , stratify=labels_2)

# **For SVCD Dataset**

In [ ]:
!kaggle datasets download -d toluwaniaremu/smartcity-cctv-violence-detection-dataset-scvd --unzip -p /content/svcd

import os

base_dir = '/content/svcd'
for root, dirs, files in os.walk(base_dir):
    print(root, ":", len(files), "files")
BASE_DIR_train = '/content/svcd/SCVD/SCVD_converted_sec_split/Train'  # '/content/svcd/SCVD/SCVD_converted/Train' # for the smaller dataset
BASE_DIR_test = '/content/svcd/SCVD/SCVD_converted_sec_split/Test'    # '/content/svcd/SCVD/SCVD_converted/Test' # for the smaller dataset

Dataset URL: https://www.kaggle.com/datasets/toluwaniaremu/smartcity-cctv-violence-detection-dataset-scvd
License(s): CC-BY-NC-SA-4.0
 98% 1.00G/1.03G [00:06<00:00, 204MB/s]
100% 1.03G/1.03G [00:06<00:00, 161MB/s]
/content/svcd : 0 files
/content/svcd/SCVD : 0 files
/content/svcd/SCVD/SCVD_converted_sec_split : 0 files
/content/svcd/SCVD/SCVD_converted_sec_split/Test : 0 files
/content/svcd/SCVD/SCVD_converted_sec_split/Test/Weaponized : 190 files
/content/svcd/SCVD/SCVD_converted_sec_split/Test/Normal : 169 files
/content/svcd/SCVD/SCVD_converted_sec_split/Test/Violence : 118 files
/content/svcd/SCVD/SCVD_converted_sec_split/Train : 0 files
/content/svcd/SCVD/SCVD_converted_sec_split/Train/Weaponized : 832 files
/content/svcd/SCVD/SCVD_converted_sec_split/Train/Normal : 872 files
/content/svcd/SCVD/SCVD_converted_sec_split/Train/Violence : 970 files
/content/svcd/SCVD/SCVD_converted : 0 files
/content/svcd/SCVD/SCVD_converted/Test : 0 files
/content/svcd/SCVD/SCVD_converted/Test/Weapo

In [ ]:
def prepare_data(base_path):
    label_map = {
        "Violence": 0,            # Class 0
        "Weaponized": 0 ,        # Class 0
        "Normal": 1              # Class 1
    }

    file_paths = []
    labels = []

    # Loop through each class folder (Normal, Violence, Weaponized)
    for class_name, label in label_map.items():
        class_path = os.path.join(base_path, class_name)

        # Collect all video file paths in the current class folder
        for file_name in os.listdir(class_path):
            if file_name.endswith(('.mp4', '.avi', '.mov')):  # Adjust for valid video formats
                file_paths.append(os.path.join(class_path, file_name))
                labels.append(label)


    file_paths = np.array(file_paths)

    labels = np.array(labels)

    # Shuffle data while keeping labels in sync
    indices = np.arange(len(file_paths))  # Create an array of indices
    np.random.shuffle(indices)             # Shuffle the indices

    # Use the shuffled indices to rearrange file_paths and labels
    shuffled_file_paths = file_paths[indices]
    shuffled_labels = labels[indices]
    # Convert lists to numpy arrays for easier handling
    return shuffled_file_paths, shuffled_labels

In [ ]:


file_paths_3_tr , labels_3_tr = prepare_data(BASE_DIR_train)
file_paths_3_ts , labels_3_ts = prepare_data(BASE_DIR_test)

file_paths_3 = np.concatenate((file_paths_3_tr , file_paths_3_ts))
labels_3 = np.concatenate((labels_3_tr , labels_3_ts))



for path in file_paths_3_tr:
  frame_count = get_frame_count(path)
  print(f"Total number of frames: {frame_count}")

Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
Total number of frames: 30
T

In [ ]:
X_train , y_train = file_paths_3_tr , labels_3_tr
X_test , y_test = file_paths_3_ts , labels_3_ts

# **For Dataset 4**

In [ ]:
!git clone https://github.com/airtlab/A-Dataset-for-Automatic-Violence-Detection-in-Videos.git /content/violence-detection-dataset

Cloning into '/content/violence-detection-dataset'...
remote: Enumerating objects: 376, done.
remote: Counting objects: 100% (12/12), done.
remote: Compressing objects: 100% (9/9), done.
remote: Total 376 (delta 3), reused 11 (delta 3), pack-reused 364 (from 1)
Receiving objects: 100% (376/376), 1.02 GiB | 54.80 MiB/s, done.
Resolving deltas: 100% (3/3), done.
Updating files: 100% (355/355), done.


In [ ]:
def prepare_data(base_path):

    categories = {
        "violent": 0,         # Class 0
        "non-violent": 1      # Class 1
    }

    file_paths = []
    labels = []

    # Iterate through each category (violent and non-violent)
    for category, label in categories.items():
        category_path = os.path.join(base_path, category)

        # Explore each cam subdirectory within the category
        for cam_folder in ["cam1", "cam2"]:
            cam_path = os.path.join(category_path, cam_folder)
            if os.path.isdir(cam_path):
                for file_name in os.listdir(cam_path):
                    if file_name.endswith('.mp4'):
                        file_paths.append(os.path.join(cam_path, file_name))
                        labels.append(label)

    # Convert lists to numpy arrays and shuffle data
    file_paths = np.array(file_paths)
    labels = np.array(labels)
    indices = np.arange(len(file_paths))
    np.random.shuffle(indices)
    shuffled_file_paths = file_paths[indices]
    shuffled_labels = labels[indices]

    return shuffled_file_paths, shuffled_labels

In [ ]:
def get_frame_count(video_path):
    # Open the video file
    cap = cv2.VideoCapture(video_path)

    # Check if the video opened successfully
    if not cap.isOpened():
        print(f"Error: Cannot open video {video_path}")
        return None

    # Get the total number of frames
    frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))

    # Release the video capture object
    cap.release()

    return frame_count

base_dir = '/content/violence-detection-dataset/violence-detection-dataset'
file_paths_4, labels_4 = prepare_data(base_dir)


for path in file_paths_4:
  frame_count = get_frame_count(path)
  print(f"Total number of frames: {frame_count}")

Total number of frames: 134
Total number of frames: 165
Total number of frames: 125
Total number of frames: 87
Total number of frames: 189
Total number of frames: 337
Total number of frames: 169
Total number of frames: 168
Total number of frames: 350
Total number of frames: 124
Total number of frames: 138
Total number of frames: 130
Total number of frames: 192
Total number of frames: 102
Total number of frames: 102
Total number of frames: 116
Total number of frames: 214
Total number of frames: 147
Total number of frames: 126
Total number of frames: 369
Total number of frames: 186
Total number of frames: 219
Total number of frames: 159
Total number of frames: 117
Total number of frames: 350
Total number of frames: 227
Total number of frames: 150
Total number of frames: 337
Total number of frames: 151
Total number of frames: 160
Total number of frames: 105
Total number of frames: 192
Total number of frames: 160
Total number of frames: 230
Total number of frames: 369
Total number of frame

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(file_paths_4 , labels_4 , test_size=0.2 , random_state=42, stratify=labels_4)

# **Test section (the pretrained 3D class)**

In [ ]:
import torch
import torch.nn as nn
import torchvision
import cv2
import numpy as np

class MyModel(nn.Module):
    def __init__(self, num_classes=1):
        super(MyModel, self).__init__()  # Initialize nn.Module
        # Load a pre-trained 3D ResNet (R3D-18) model
        self.model = torchvision.models.video.r3d_18(pretrained=True)

        # Modify the final layer for binary classification
        self.model.fc = nn.Linear(self.model.fc.in_features, num_classes)

        # Use binary cross-entropy for binary classification
        self.criterion = nn.BCEWithLogitsLoss()
        self.optimizer = torch.optim.Adam(self.model.parameters(), lr=1e-4)

    def preprocess_video(self, video_path, num_frames=40):
        """Preprocess video: sample frames, resize, normalize, and return tensor."""
        cap = cv2.VideoCapture(video_path)
        total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
        frame_indices = np.linspace(0, total_frames - 1, num=num_frames, dtype=int)
        sampled_frames = []

        for idx in frame_indices:
            cap.set(cv2.CAP_PROP_POS_FRAMES, idx)
            ret, frame = cap.read()
            if not ret:
                continue
            frame = cv2.resize(frame, (112, 112))  # Resize to 112x112 for R3D-18
            frame = np.transpose(frame, (2, 0, 1))  # Channels-first
            sampled_frames.append(frame)

        cap.release()

        if len(sampled_frames) < num_frames:
            padding = np.zeros((num_frames - len(sampled_frames), 3, 112, 112))
            sampled_frames = np.concatenate([sampled_frames, padding], axis=0)

        # Convert to tensor and rearrange dimensions to (3, num_frames, 112, 112)
        return torch.tensor(sampled_frames).float().permute(1, 0, 2, 3).unsqueeze(0)

    def train_model(self, video_paths, labels, batch_size=30):
        """Train the model in mini-batches."""
        self.model.train()
        for i in range(0, len(video_paths), batch_size):
            batch_videos = video_paths[i:i + batch_size]
            batch_labels = torch.tensor(labels[i:i + batch_size]).float().unsqueeze(1)

            X_batch = torch.cat([self.preprocess_video(path) for path in batch_videos])
            y_batch = batch_labels

            self.optimizer.zero_grad()
            outputs = self.model(X_batch)
            loss = self.criterion(outputs, y_batch)
            loss.backward()
            self.optimizer.step()
            print(f"Batch {i // batch_size + 1}: Loss = {loss.item():.4f}")


    def forward(self, x):
        return self.model(x)

    def test(self, video_paths, labels):
        """Test the model on the given videos and compute accuracy."""
        self.model.eval()

        predictions = []

        with torch.no_grad():
            for i, video_path in enumerate(video_paths):
                # Preprocess the video and get the label
                X = self.preprocess_video(video_path)
                # X = X.to(self.device)  # Move data to the same device as the model

                # Make prediction
                output = self.model(X)
                pred = torch.sigmoid(output)  # Apply sigmoid for binary classification
                pred_label = (pred >= 0.5).float()  # Threshold at 0.5

                # Track predictions
                predictions.append(pred_label.item())


        return predictions

    def save_model(self, filepath):
        torch.save({
            'model_state_dict': self.state_dict(),
        }, filepath)
        print(f"Model saved to {filepath}.")

    @staticmethod
    def load_model(filepath, num_classes=1):
        model = MyModel(num_classes)
        checkpoint = torch.load(filepath, weights_only=True)  # Set weights_only=True
        model.load_state_dict(checkpoint['model_state_dict'])
        # model.optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
        model.eval()  # Set to evaluation mode
        print(f"Model loaded from {filepath}.")
        return model







In [ ]:
model = MyModel().load_model('/content/pre_3D_model_v2.h5') # change the path to the chosen .h5 file


Model loaded from /content/pre_3D_model_v2.h5.


In [ ]:
for i in range(2):   # modify number of epochs
  model.train_model(X_train, y_train)

Batch 1: Loss = 0.0075
Batch 2: Loss = 0.0143
Batch 3: Loss = 0.0096
Batch 4: Loss = 0.0152
Batch 5: Loss = 0.0052
Batch 6: Loss = 0.0109
Batch 7: Loss = 0.0076
Batch 8: Loss = 0.0106
Batch 9: Loss = 0.0181
Batch 10: Loss = 0.0088
Batch 11: Loss = 0.0058
Batch 12: Loss = 0.0071
Batch 13: Loss = 0.0082
Batch 14: Loss = 0.0045
Batch 15: Loss = 0.0184
Batch 16: Loss = 0.0143
Batch 17: Loss = 0.0237
Batch 18: Loss = 0.0043
Batch 19: Loss = 0.0138
Batch 20: Loss = 0.0129
Batch 21: Loss = 0.0031
Batch 22: Loss = 0.0192
Batch 23: Loss = 0.0067
Batch 24: Loss = 0.0158
Batch 25: Loss = 0.0050
Batch 26: Loss = 0.0047
Batch 27: Loss = 0.0165
Batch 28: Loss = 0.0109
Batch 29: Loss = 0.0041
Batch 1: Loss = 0.0029
Batch 2: Loss = 0.0091
Batch 3: Loss = 0.0043
Batch 4: Loss = 0.0030
Batch 5: Loss = 0.0023
Batch 6: Loss = 0.0051
Batch 7: Loss = 0.0041
Batch 8: Loss = 0.0027
Batch 9: Loss = 0.0036
Batch 10: Loss = 0.0060
Batch 11: Loss = 0.0029
Batch 12: Loss = 0.0026
Batch 13: Loss = 0.0030
Batch 14: 

In [ ]:
model.save_model('/content/pre_3D_model_v2.h5')

Model saved to /content/pre_3D_model_v2.h5.


In [ ]:
pred = model.test(X_test, y_test)

In [ ]:
calculate_accuracy(pred, y_test)

98.0

# **For Normal Models**

In [ ]:
model = NormalModel()
model.load_model('/content/3D_CNN_model.h5') # change the path to the chosen .h5 file



In [ ]:
model.train(X_train, y_train)


In [ ]:
pred = model.test(X_test)

calculate_accuracy(pred, y_test)


In [ ]:
model.save_model('/content/3D_CNN_model.h5')

# **For saving the model in the drive**

In [ ]:

import zipfile
import shutil

h5_file_path = '/content/content/pre_3D_model_v2.h5'    # path of the .h5 file
zip_file_path = '/content/pre_3D_model.zip'  # Path to save the zip file


with zipfile.ZipFile(zip_file_path, 'w') as zipf:
    zipf.write(h5_file_path, arcname='/content/pre_3D_model.h5')  # here will be the name inside the .zip file


shutil.move(zip_file_path, '/content/drive/MyDrive/Models/pre_3D_model.zip')  # change which file in the folder to overwrite


'/content/drive/MyDrive/Models/pre_3D_model.zip'

# **Test across all models**

first, load the corresponding dataset from above header

In [ ]:
Dataset_name = 'real-life Violence'            # change the name

model_1 = NormalModel()
model_1.load_model('/content/A_model.h5')
model_1_result = calculate_accuracy(model_1.test(X_test) , y_test)

model_2 = NormalModel()
model_2.load_model('/content/model.h5')
model_2_result = calculate_accuracy(model_2.test(X_test) , y_test)

model_3 = MyModel().load_model('/content/pre_3D_model.h5')
model_3_result = calculate_accuracy(model_3.test(X_test , y_test) , y_test)

print(f'The accuracy of first model (one LSTM) on the {Dataset_name} dataset = {model_1_result}%')
print(f'The accuracy of first model (Bi LSTM) on the {Dataset_name} dataset = {model_2_result}%')
print(f'The accuracy of first model (pre-trained 3D) on the {Dataset_name} dataset = {model_3_result}%')

Model loaded from /content/A_model.h5.
1/1 [==============================] - 1s 746ms/step
Model loaded from /content/model.h5.
1/1 [==============================] - 1s 713ms/step


/usr/local/lib/python3.10/dist-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=R3D_18_Weights.KINETICS400_V1`. You can also use `weights=R3D_18_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


Model loaded from /content/pre_3D_model.h5.
The accuracy of first model (one LSTM) on the real-life Violence dataset = 87.75%
The accuracy of first model (Bi LSTM) on the real-life Violence dataset = 50.0%
The accuracy of first model (pre-trained 3D) on the real-life Violence dataset = 52.25%


# **For training the pre-trained 3D over all datasets**

In [ ]:
all_data = np.array([], dtype=object)
all_labels = np.array([], dtype=int)

# np.random.seed(42)

file_paths = [file_paths_1, file_paths_2, file_paths_3, file_paths_4]
labels = [labels_1, labels_2, labels_3 , labels_4]

for paths, classes in zip(file_paths, labels):
    all_data = np.concatenate((all_data, np.array(paths, dtype=object)))
    all_labels = np.concatenate((all_labels, np.array(classes, dtype=int)))

indices = np.arange(all_data.shape[0])
np.random.shuffle(indices)
all_data = all_data[indices]
all_labels = all_labels[indices]

X_train , X_test, y_train, y_test = train_test_split(all_data , all_labels , test_size = 0.2 ,  stratify=all_labels)


print(len(X_train) , len(y_train) , len(X_test) , len(y_test))

5200 5200 1301 1301


In [ ]:
model = MyModel().load_model('/content/content/pre_3D_model_v2.h5')

/usr/local/lib/python3.10/dist-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=R3D_18_Weights.KINETICS400_V1`. You can also use `weights=R3D_18_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
Downloading: "https://download.pytorch.org/models/r3d_18-b3b3357e.pth" to /root/.cache/torch/hub/checkpoints/r3d_18-b3b3357e.pth
100%|██████████| 127M/127M [00:00<00:00, 216MB/s]


Model loaded from /content/content/pre_3D_model_v2.h5.


In [ ]:
model.train_model(X_train , y_train)

/usr/local/lib/python3.10/dist-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=R3D_18_Weights.KINETICS400_V1`. You can also use `weights=R3D_18_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
Downloading: "https://download.pytorch.org/models/r3d_18-b3b3357e.pth" to /root/.cache/torch/hub/checkpoints/r3d_18-b3b3357e.pth
100%|██████████| 127M/127M [00:00<00:00, 211MB/s]


Model loaded from /content/pre_3D_model.h5.


<ipython-input-18-c8d9d4fb9314>:43: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at ../torch/csrc/utils/tensor_new.cpp:278.)
  return torch.tensor(sampled_frames).float().permute(1, 0, 2, 3).unsqueeze(0)


Batch 1: Loss = 0.3940
Batch 2: Loss = 0.3259
Batch 3: Loss = 0.2759
Batch 4: Loss = 0.1498
Batch 5: Loss = 0.3804
Batch 6: Loss = 0.5726
Batch 7: Loss = 0.2009
Batch 8: Loss = 0.1653
Batch 9: Loss = 0.1218
Batch 10: Loss = 0.3490
Batch 11: Loss = 0.2296
Batch 12: Loss = 0.2138
Batch 13: Loss = 0.0973
Batch 14: Loss = 0.0951
Batch 15: Loss = 0.2510
Batch 16: Loss = 0.1758
Batch 17: Loss = 0.2845
Batch 18: Loss = 0.1654
Batch 19: Loss = 0.1044
Batch 20: Loss = 0.1124
Batch 21: Loss = 0.1571
Batch 22: Loss = 0.1967
Batch 23: Loss = 0.2451
Batch 24: Loss = 0.5118
Batch 25: Loss = 0.2556
Batch 26: Loss = 0.1320
Batch 27: Loss = 0.1707
Batch 28: Loss = 0.3808
Batch 29: Loss = 0.0617
Batch 30: Loss = 0.0596
Batch 31: Loss = 0.0636
Batch 32: Loss = 0.0771
Batch 33: Loss = 0.0768
Batch 34: Loss = 0.3999
Batch 35: Loss = 0.1921
Batch 36: Loss = 0.1351
Batch 37: Loss = 0.1076
Batch 38: Loss = 0.2017
Batch 39: Loss = 0.1576
Batch 40: Loss = 0.3676
Batch 41: Loss = 0.1160
Batch 42: Loss = 0.0869
B

In [ ]:
model.save_model('/content/pre_3D_model.h5')


Model saved to /content/pre_3D_model.h5.


In [ ]:
pred = model.test(X_test, y_test)
calculate_accuracy(pred, y_test)

<ipython-input-26-436b14c8b8f7>:43: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at ../torch/csrc/utils/tensor_new.cpp:278.)
  return torch.tensor(sampled_frames).float().permute(1, 0, 2, 3).unsqueeze(0)


99.07763259031515